## Cross-validation

In [2]:
%reload_ext autoreload
%autoreload 2

In [3]:
import os
import random

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

dir_path = os.path.abspath('')
os.chdir(dir_path)

### Full matrix A

In [21]:
A=pd.read_csv('./saved_tables/save_A.csv',index_col=0)

#### Note: To save as compatible for C++
A_for_c=A.copy()
A_for_c['endline']='.'
A_for_c.to_csv("./C++ script/saved_tables/save_A.csv",index=False,header=False)

### Generate 10 matrices A_train : A with 20% of the 1s (i.e interactions) randomly removed

#### List of indices where there is a 1 in A:

In [5]:
list_ind=[]

for drug in A.columns:
    for disease in A.index:
        if A[drug][disease]==1:
            list_ind.append((drug,disease))

#### Number of 1 to remove

In [6]:
to_remove=int(len(list_ind)*0.2)

#### Choosing the lists of list of elements to remove

In [7]:
random.seed(42)

# List of the list of indices to remove each time
lists_to_remove=[]
for i in range(10):
    lists_to_remove.append(random.sample(list_ind,to_remove))
    

#### Generating the tables and saving them in C++ compatible form

In [43]:
for i in range(10):
    A_train=A.copy()
    indices=lists_to_remove[i]
    
    for couple in indices:
        drug=couple[0]
        disease=couple[1]
        
        A_train[drug][disease]=0
        

    A_train['endline']='.'
    A_train.to_csv("./C++ script/A_tables/A_train_"+str(i+1)+".csv",index=False,header=False)

### Final similarity matrices

The S_td matrices were computed and stored via C++, we can now generate for each one 9 final similarity matrices with different $\alpha$s.

In [47]:
alphas=[0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9]
S_disease_0=pd.read_csv('./saved_tables/save_disease_sim_norm.csv',index_col=0)

In [49]:
for i in range(10):
    # Path for each S_td
    path_S_td="./C++ script/Std_tables/S_td_"+str(i+1)+".csv"
    
    # Loading the S_td tables and adding index and headers
    S_td=pd.read_csv(path_S_td,header=None)
    S_td.columns=A.index
    S_td.index=A.index
    
    for alpha in alphas:
        S= alpha * S_disease_0 + (1-alpha) * S_td
        S['endline']='.'
        S.to_csv("./C++ script/S_tables/S_"+str(i+1)+'_'+'{:.2f}'.format(round(alpha, 2))+".csv",index=False,header=False)


Now we can access the similarity matrix for the ith partitionned A and with $\alpha$ by *"./C++ script/S\_tables/S\_i\_$\alpha$.csv"*

### We generated the 810 weight matrices associated to the 81 couples of variables and 10 random splits

#### No we want to evaluate the capacity of the algorithm to recover the lost associations

In [13]:
alphas=[0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9]
lambdas=[0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9]

In [89]:
nb_deleted=to_remove

top_score1=0
top_score2=0

for alpha in alphas:
    for lambd in lambdas:
        count1=0 # To count the nb of recovered associations in top X
        count2=0 # 2nd metric where we look at recovered with association >0 even of not in top X
        
        for i in range(10): #Testing on the 10 splits

            deleted=lists_to_remove[i]
            
            # Loading the corresponding weight and association matrices
            path_W="./C++ script/W_tables/W_"+str(i+1)+"_"+'{:.2f}'.format(round(alpha, 2))+"_"+'{:.2f}'.format(round(lambd, 2))+".csv"
            W=pd.read_csv(path_W,header=None)
            W.columns=A.index
            W.index=A.index
       
            path_A="./C++ script/A_tables/A_train_"+str(i+1)+".csv"
            A_train=pd.read_csv(path_A,header=None)
            A_train=A_train.drop(2115,axis=1)
            A_train.columns=A.columns
            A_train.index=A.index

            
            # Compute recommendations 
            R= W@A_train
            

            # Check if deleted drug-disease associations are recovered in the TOP X per disease
            # where X is the number of drugs associated to the disease
            # OR metric2: just if predicted >0 without looking at top
            for drug,disease in deleted:
                top=np.sum(A.loc[disease,:])+10
                
                top_assos=R[R.index==disease].T.sort_values(disease,ascending=False)
                
                if top_assos[disease][drug]>0:
                    count2+=1
                    if drug in top_assos[disease][:top]: # Check if in top X
                        count1+=1

        # Average of percentage of links "recovered"
        recovered1 = count1/(10*nb_deleted)
        recovered2 = count2/(10*nb_deleted)

        if recovered1 > top_score1:
            top_score1 = recovered1
            top_alpha1 =alpha
            top_lambda1 =lambd
            
        if recovered2 > top_score2:
            top_score2 = recovered2
            top_alpha2 =alpha
            top_lambda2 =lambd

### Results of the best parameters

In [90]:
print('The best score for metric 1 was:','{:.2%}'.format(top_score1),"\nObtained with alpha="+str(top_alpha1)+" and lambda="+str(top_lambda1))

The best score for metric 1 was: 61.54% 
Obtained with alpha=0.1 and lambda=0.1


In [91]:
print('The best score for metric 2 was:','{:.2%}'.format(top_score2),"\nObtained with alpha="+str(top_alpha2)+" and lambda="+str(top_lambda2))

The best score for metric 2 was: 74.56% 
Obtained with alpha=0.1 and lambda=0.1


## Computation of final matrices with best parameters

### Importing table drug_disease_asso to get the names of the diseases when available

In [56]:
drug_disease_associations=pd.read_csv('data/drug_disease_associations.csv')
drug_disease_asso=drug_disease_associations.drop(['Unnamed: 0'],axis=1).set_index(['drug_name'])
drug_disease_asso=drug_disease_asso[drug_disease_asso['status']=='Approved']

drug_disease_asso['ind_id']=drug_disease_asso['ind_id'].str.lower()
drug_disease_asso['drug_id']=drug_disease_asso['drug_id'].str.lower()
drug_disease_asso['ind_name']=drug_disease_asso['ind_name'].str.lower()
drug_disease_asso.index=drug_disease_asso.index.str.lower()

### Final weight matrix

In [92]:
path_W="./C++ script/W_final_tables/W_"+'{:.2f}'.format(round(top_alpha1, 2))+"_"+'{:.2f}'.format(round(top_lambda1, 2))+".csv"
W=pd.read_csv(path_W,header=None)
W.columns=A.index
W.index=A.index

### Final recommendations

In [93]:
reco = W @ A

# Normalize Reco
reco = (reco-np.min(reco))/(np.max(reco)-np.min(reco))


#Display results :first 10 recommendations next to the ones given in the drug_disease_association table
for disease in reco.index:
    
    try:# we do not always have
        disease_name=np.unique(drug_disease_asso[drug_disease_asso['ind_id']==disease]['ind_name'])[0]
    except:
        disease_name=disease
    
    # Formatting the recommendation scores for the disease
    reco_disease=reco[reco.index==disease].T.sort_values(disease,ascending=False)
    reco_disease=reco_disease.rename(columns={disease:disease_name})
    reco_disease.index.names = ['drug']
    
    # What was recommended before
    reco_before=A[A.index==disease].T.rename(columns={disease:'previous reco'})

    display(pd.concat([reco_disease,reco_before],axis=1, sort=False).head(10))



ind_id                   incomplete spontaneous abortion  previous reco
oxytocin                                        0.974801              1
dinoprost tromethamine                          0.619255              1
dinoprostone                                    0.619255              1
mifepristone                                    0.588218              0
carboprost tromethamine                         0.370448              0
misoprostol                                     0.075413              0
ergonovine                                      0.075413              0
methylergometrine                               0.075413              0
olsalazine                                      0.000000              0
oprelvekin                                      0.000000              0

ind_id                                    renal tubular acidosis  \
sodium phosphate, monobasic, monohydrate                1.000000   
potassium citrate                                       1.000000   
allopurinol                                             1.000000   
l-aspartic acid                                         1.000000   
potassium chloride                                      0.716513   
calcium chloride                                        0.255315   
oxytocin                                                0.000000   
oritavancin                                             0.000000   
oprelvekin                                              0.000000   
ondansetron                                             0.000000   

ind_id                                    previous reco  
sodium phosphate, monobasic, monohydrate              0  
potassium citrate                                     1  
allopurinol                                           0  
l-aspartic acid                                       0  
potassium chloride                                    0  
calcium chloride                                      0  
oxytocin                                              0  
oritavancin                                           0  
oprelvekin                                            0  
ondansetron                                           0

ind_id             acne vulgaris  previous reco
adapalene               0.219360              1
azelaic acid            0.219360              1
benzoyl peroxide        0.109746              1
norgestimate            0.066932              1
ethinyl estradiol       0.049624              1
drospirenone            0.049624              1
gramicidin d            0.044346              0
tetracycline            0.039025              1
estrone sulfate         0.036951              0
norethisterone          0.034722              1

ind_id         acromegaly  previous reco
pegvisomant      1.000000              1
lisuride         0.529859              1
bromocriptine    0.291553              1
lanreotide       0.208646              1
octreotide       0.208646              1
levodopa         0.095902              0
carbidopa        0.095902              0
rasagiline       0.070826              0
cycrimine        0.070826              0
entacapone       0.070826              0

ind_id         hypersomatotropic gigantism  previous reco
lanreotide                        1.000000              1
pegvisomant                       0.772644              0
lisuride                          0.381525              0
bromocriptine                     0.211878              0
octreotide                        0.132879              0
abacavir                          0.000000              0
olsalazine                        0.000000              0
oritavancin                       0.000000              0
orciprenaline                     0.000000              0
oprelvekin                        0.000000              0

...

ind_id                    c3897522  previous reco
abacavir                       0.0              0
olopatadine                    0.0              0
oritavancin                    0.0              0
orciprenaline                  0.0              0
oprelvekin                     0.0              0
ondansetron                    0.0              0
omeprazole                     0.0              0
omega-3-carboxylic acids       0.0              0
ombitasvir                     0.0              0
omalizumab                     0.0              0

ind_id                    c3897523  previous reco
abacavir                       0.0              0
olopatadine                    0.0              0
oritavancin                    0.0              0
orciprenaline                  0.0              0
oprelvekin                     0.0              0
ondansetron                    0.0              0
omeprazole                     0.0              0
omega-3-carboxylic acids       0.0              0
ombitasvir                     0.0              0
omalizumab                     0.0              0

ind_id              osteolytic lesions of multiple myeloma  previous reco
zoledronic acid                                   1.000000              1
pamidronate                                       1.000000              1
alendronic acid                                   0.517569              0
salmon calcitonin                                 0.517569              0
risedronate                                       0.463501              0
tiludronate                                       0.428709              0
raloxifene                                        0.160766              0
teriparatide                                      0.160766              0
bazedoxifene                                      0.160766              0
strontium ranelate                                0.160766              0

ind_id               asthma-chronic obstructive pulmonary disease overlap syndrome  \
aminophylline                                                 1.000000               
theophylline                                                  1.000000               
dyphylline                                                    1.000000               
salbutamol                                                    0.747449               
pirbuterol                                                    0.429844               
ipratropium bromide                                           0.395754               
orciprenaline                                                 0.287793               
lomefloxacin                                                  0.285563               
cyclacillin                                                   0.273102               
ephedrine                                                     0.243013               

ind_id               previous reco  
aminophylline                    1  
theophylline                     1  
dyphylline                       1  
salbutamol                       0  
pirbuterol                       0  
ipratropium bromide              0  
orciprenaline                    0  
lomefloxacin                     0  
cyclacillin                      0  
ephedrine                        0

ind_id                    alopecia, male pattern  previous reco
finasteride                             1.000000              1
alfuzosin                               1.000000              0
tamsulosin                              1.000000              0
terazosin                               1.000000              0
silodosin                               1.000000              0
doxazosin                               1.000000              0
dutasteride                             1.000000              0
tadalafil                               0.507698              0
omega-3-carboxylic acids                0.000000              0
ombitasvir                              0.000000              0